## FileInput

In [3]:
import io
import panel as pn
pn.extension()

In [2]:
from panel.theme import Material

pn.config.design = Material

In [10]:
file_input = pn.widgets.FileInput(accept=".gpx")
file_input.accept = ".gpx"

file_input

BokehModel(combine_events=True, render_bundle={'docs_json': {'703ea656-d55d-406d-ba4b-eb64f99d4844': {'version…

In [11]:
import gpxpy

if file_input.value:
    gpx = gpxpy.parse(file_input.value)

In [20]:
gpx.tracks[0].segments[0]

GPXTrackSegment(points=[...])

## Map

In [13]:
import folium

m = folium.Map(location=[56.945695, 24.120704], zoom_start=13, tiles='https://{s}.basemaps.cartocdn.com/rastertiles/voyager/{z}/{x}/{y}{r}.png', attr='<a href="https://carto.com/attributions">CARTO</a>',)
folium_pane = pn.pane.plot.Folium(m, height=600)

folium_pane

BokehModel(combine_events=True, render_bundle={'docs_json': {'a6186638-036d-498e-b62f-6e2a96f0f4c7': {'version…

## FileInput + Map

Tutorial: [Visualize GPX](https://betterdatascience.com/data-science-for-cycling-how-to-visualize-gpx-strava-routes-with-python-and-folium/)

In [126]:
import panel as pn
pn.extension()

from panel.theme import Material

pn.config.design = Material

In [129]:
import gpxpy

# Accept a GPX file
file_input = pn.widgets.FileInput(accept=".gpx")

file_input

BokehModel(combine_events=True, render_bundle={'docs_json': {'5f6453a5-123f-4e04-89a8-c83e161963b9': {'version…

In [130]:
if file_input.value:
    gpx = gpxpy.parse(file_input.value)

In [131]:
import folium

route_map = folium.Map(
    tiles='https://{s}.basemaps.cartocdn.com/rastertiles/voyager/{z}/{x}/{y}{r}.png',
    attr='<a href="https://carto.com/attributions">CARTO</a>',
)

folium_pane = pn.pane.plot.Folium(route_map, height=600)

In [132]:
coordinates = [(point.latitude, point.longitude) for point in gpx.tracks[0].segments[0].points]
folium.PolyLine(coordinates, weight=6).add_to(route_map)

In [134]:
route_map.fit_bounds(route_map.get_bounds(), padding=(30, 30))

In [135]:
route_map

## Find rest times from .gpx

In [136]:
import panel as pn
pn.extension()

from panel.theme import Material

pn.config.design = Material

In [137]:
import gpxpy

# Accept a GPX file
file_input = pn.widgets.FileInput(accept=".gpx")

file_input

BokehModel(combine_events=True, render_bundle={'docs_json': {'e5267bf9-c5ca-4244-b6dc-bfeb33fb4610': {'version…

In [138]:
if file_input.value:
    gpx = gpxpy.parse(file_input.value)

In [141]:
gpx.tracks[0].segments[0].points[1].time - gpx.tracks[0].segments[0].points[0].time

datetime.timedelta(seconds=1)

In [185]:
import geopy.distance

course = gpx.tracks[0].segments[0]

tracking_rest = False

rest_lat = None
rest_lon = None
elapsed_time = 0
rest_time = 0
stop_separation = 0

# If the stop time is less than the threshold, stop is ignored
rest_threshold = 20

# If distance between stops is less than the threshold, stops are counted as one
spatial_threshold = 5  # meters

rest_times = []

start_time = course.points[0].time

for idx, point in enumerate(course.points[1:]):
    # Since we start from 2nd point, enumerate idx is already lagging by 1
    previous_point = course.points[idx]
    dt = point.time - previous_point.time
    
    dlat = point.latitude - previous_point.latitude
    dlon = point.longitude - previous_point.longitude
    
    if dlat == 0 and dlon == 0:
        
        if not tracking_rest:
            tracking_rest = True
            elapsed_time = (previous_point.time - start_time).seconds
            rest_lat = previous_point.latitude
            rest_lon = previous_point.longitude
            
        rest_time += dt.seconds
        
    elif rest_time != 0 and len(rest_times) == 0:
        rest_times.append([rest_lat, rest_lon, elapsed_time, rest_time, False])
        
    elif rest_time != 0 and len(rest_times) > 0:
        
        # Distance between this and previous stop
        previous_stop = rest_times[-1]
        prev_stop_coords = tuple(previous_stop[:2])
        stop_separation = geopy.distance.distance(prev_stop_coords, (rest_lat, rest_lon)).meters
        
        if rest_time > rest_threshold and stop_separation < spatial_threshold:
            previous_stop[3] += rest_time
            previous_stop[4] = True
            rest_times[-1] = previous_stop
        elif rest_time > rest_threshold:
            rest_times.append([rest_lat, rest_lon, elapsed_time, rest_time, False])
        
        rest_lat, rest_lon = None, None
        rest_time, elapsed_time, stop_separation = 0, 0, 0
        tracking_rest = False
       
(len(rest_times), rest_times)
        

(14,
 [[55.678989, 26.045567, 668, 12, False],
  [55.367126, 25.990673, 17204, 55, False],
  [55.315269, 26.124268, 20437, 37, False],
  [55.141258, 25.814508, 31410, 112, True],
  [55.266376, 25.775789, 44291, 1167, True],
  [55.332256, 25.721594, 52262, 71, False],
  [55.332687, 25.718582, 52401, 190, True],
  [55.278694, 25.566046, 56455, 220, False],
  [55.308754, 25.586226, 59618, 135, False],
  [55.400677, 25.870913, 67820, 167, False],
  [55.528027, 25.843555, 72993, 221, True],
  [55.558071, 25.958256, 76459, 23, False],
  [55.574924, 25.973749, 77574, 114, False],
  [55.591019, 25.970882, 78461, 31, False]])

### Add rest time locations on map

In [186]:
route_map = folium.Map(
    tiles='https://{s}.basemaps.cartocdn.com/rastertiles/voyager/{z}/{x}/{y}{r}.png',
    attr='<a href="https://carto.com/attributions">CARTO</a>',
)

coordinates = [(point.latitude, point.longitude) for point in gpx.tracks[0].segments[0].points]
folium.PolyLine(coordinates, weight=6).add_to(route_map)

route_map.fit_bounds(route_map.get_bounds(), padding=(30, 30))

start_lat = course.points[0].latitude
start_lon = course.points[0].longitude

fin_lat = course.points[0].latitude
fin_lon = course.points[0].longitude

# Start position marker
folium.Marker([start_lat, start_lon], icon=folium.Icon(icon="play", prefix="fa", color="green")).add_to(route_map)

# Finish position marker
folium.Marker([fin_lat, fin_lon], icon=folium.Icon(icon="flag-checkered", prefix="fa", color="red")).add_to(route_map)

marker_colors = ["lightgreen", ""]

for stop in rest_times:
    lat, lon = stop[:2]
    stop_time = stop[3]
        
    if stop_time < 60:  # 10 minutes
        icon_color = "lightgreen"
        
    elif stop_time < 5 * 60:  # 5 minutes
        icon_color = "orange"
    
    else:
        icon_color = "lightred"
        
    
    folium.Marker([lat, lon], icon=folium.Icon(color=icon_color)).add_to(route_map)
    
route_map

## Basic Layout

- GridSpec

In [1]:
import panel as pn
pn.extension()

In [24]:
import gpxpy

# Accept a GPX file
file_input = pn.widgets.FileInput(accept=".gpx")

In [25]:
multi_choice = pn.widgets.MultiChoice(name='MultiSelect',
    options=['Resupply', 'Mechanical', 'Sleep', 'Rest'])

ctrl_col = pn.Column('# Step 1: Choose a race .gpx file', file_input, multi_choice)

In [105]:
import folium

route_map = folium.Map(location=[56.945695, 24.120704], zoom_start=13, tiles='https://{s}.basemaps.cartocdn.com/rastertiles/voyager/{z}/{x}/{y}{r}.png', attr='<a href="https://carto.com/attributions">CARTO</a>',)
folium_pane = pn.pane.plot.Folium(route_map, height=600)

map_col = pn.Column(folium_pane)

In [106]:
gspec = pn.GridSpec(sizing_mode='stretch_both', min_height=800)

gspec[:, 0] = ctrl_col
gspec[:, 1:5] = route_map

In [118]:
gspec

BokehModel(combine_events=True, render_bundle={'docs_json': {'85f75244-a4ba-4638-8414-0825f403eb68': {'version…

In [119]:
if file_input.value:
    gpx = gpxpy.parse(file_input.value)

In [120]:
gpx

GPX(tracks=[GPXTrack(name='Winter Epic 2023', segments=[GPXTrackSegment(points=[...])])])

In [121]:
import numpy as np

lats = np.array([point.latitude for point in gpx.tracks[0].segments[0].points])
lons = np.array([point.longitude for point in gpx.tracks[0].segments[0].points])

In [122]:
min_lat = np.min(lats)
max_lat = np.max(lats)

min_lon = np.min(lons)
max_lon = np.max(lons)

(min_lat, max_lat, min_lon, max_lon)

(55.126633, 55.683483, 25.526451, 26.23228)

In [90]:
folium_pane.object.location = [min_lat + (max_lat - min_lat)/2, min_lon + (max_lon - min_lon)/2]
folium_pane.object.zoom_start = 5


In [123]:
coordinates = [(point.latitude, point.longitude) for point in gpx.tracks[0].segments[0].points]
folium.PolyLine(coordinates, weight=6).add_to(route_map)

In [125]:
route_map

In [114]:
route_map.get_bounds()

[[55.126633, 25.526451], [55.683483, 26.23228]]

In [115]:
# folium_pane.object.fit_bounds([[min_lat, min_lon], [max_lat, max_lon]])
# route_map.fit_bounds([[52.193636, -2.221575], [52.636878, -1.139759]])

folium_pane.object.fit_bounds(folium_pane.object.get_bounds(), padding=(30, 30))

In [116]:
gspec

BokehModel(combine_events=True, render_bundle={'docs_json': {'c8a82c62-c385-4eb6-a36d-6c789f3e5af2': {'version…